# Trail Recommendations

List everything that we need to do.

In [ ]:
import Trailforks as tf
import TrailforksScraper as tfs
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np

## Import all the files

In [ ]:
trails_checkins = pd.read_csv('trail-checkins.csv')
trailforks_trails = pd.read_csv('trailforks-trails.csv')
wta_trails = pd.read_csv('ResultsZip.csv')

## Getting data from Trailforks

- 'activitytype=6' for hiking
- Trailstyle = Popularity

Trailforks api documentation: https://www.trailforks.com/about/api/#!/trail

Trailforks popularity heatmap: https://www.trailforks.com/region/united-states/?activitytype=6&z=10.4&lat=48.30699&lon=-120.42421&trailstyle=popularity

Trailforks popularity scores (sorted in descending order): https://www.trailforks.com/region/united-states/trails/?sort=t.popularity_score&order=desc&difficulty=2,3,4,11,9,5,6,8&activitytype=6

In [ ]:
trailForksScrapper = tfs.trailforksScrapper()

In [ ]:
# This code was used to scrate all the trails in north-carolina and washington 
# from trailforks along with their popularity.

# north_carolina = trailForksScrapper.fetchTrailsByRegionAndPages('north-carolina',23)
# washington = trailForksScrapper.fetchTrailsByRegionAndPages('washington',72)

Convert trail titles to have only words separated by -
This will be used in url for scraping checkins.

In [ ]:
# north_carolina['title'] = north_carolina['title'].str.replace('\W', ' ').str.lower()
# north_carolina['title'] = north_carolina['title'].str.replace('[^a-z A-Z]', '').str.strip().str.replace(' ','-')
# washington['title'] = washington['title'].str.replace('\W', ' ').str.lower()
# washington['title'] = washington['title'].str.replace('[^a-z A-Z]', '').str.strip().str.replace(' ','-')

Getting trail stats for all the trails collected previously.

In [ ]:
# This code can be used to scrape trails checkins and store them in dataframe.

'''import pandas as pd 

df = pd.DataFrame()
for trail in trails:
    df_trail = trailForksScrapper.fetchTrailStats(trail)
    if df_trail is not None:
        df_trail['trail'] = trail
        df = pd.concat([df,df_trail])

df'''

## Merge all the tables to create one dataset

Cleaning up datasets:
- Removing trails with title unknown and NAN
- Removing unnamed columns
- filtering checkins greater than 0

In [ ]:
trailforks_trails = trailforks_trails.dropna(subset='title')
trailforks_trails = trailforks_trails[~trailforks_trails['title'].str.contains('unknown')]
trailforks_trails = trailforks_trails[['title','riding area','rating','distance','descent','climb','popularity_score']]
trailforks_trails['title'] = trailforks_trails['title'].str.replace('--','-')
trailforks_trails

In [ ]:
wta_trails['title_wta'] = wta_trails['TITLE']
wta_trails['title_wta'] = wta_trails['title_wta'].str.replace('\W', ' ').str.lower()
wta_trails['title_wta'] = wta_trails['title_wta'].str.replace('[^a-z A-Z]', '').str.strip().str.replace(' ','-')
wta_trails['title_wta'] = wta_trails['title_wta'].str.replace('--','-',regex=True) ## this is not working. Need to check why
wta_trails = wta_trails.drop(columns=['Unnamed: 0'])
wta_trails

In [ ]:
trails_checkins = trails_checkins[['Period','Check-Ins','trail']]
trails_checkins = trails_checkins[trails_checkins['Check-Ins']>0]
trails_checkins

Combine trailforks and wta trails data based on titles matching as substrings of each other. This needs to be done because same trails have slightly different names.

In [195]:
dataset_1 = trailforks_trails
dataset_2 = wta_trails
dataset_1['title'] = dataset_1['title'].str.replace('-trail','')
dataset_2['title_wta'] = dataset_2['title_wta'].str.replace('-trail','')
result_dataset = pd.DataFrame()
for i in range(len(dataset_2)):
    row_matched = dataset_1[dataset_1['title'].str.contains(dataset_2.iloc[i]['title_wta'])]
    if len(row_matched) > 0:
        df = dataset_2[dataset_2['title_wta']==dataset_2.iloc[i]['title_wta']]
        row_matched[df.columns] = None
        for j in range(0,len(row_matched)):
            row_matched.loc[row_matched.index[j],df.columns] = df.iloc[0]
        result_dataset = pd.concat([result_dataset,row_matched])
        
result_dataset.head()

/var/folders/7v/3vykhk5j10v0p4dt8gphqvyh0000gn/T/ipykernel_42814/3366869505.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row_matched[df.columns] = None
/var/folders/7v/3vykhk5j10v0p4dt8gphqvyh0000gn/T/ipykernel_42814/3366869505.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row_matched[df.columns] = None
/var/folders/7v/3vykhk5j10v0p4dt8gphqvyh0000gn/T/ipykernel_42814/3366869505.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[ro

title  \
545              raven-roost   
501   rainbow-ridge-bootpath   
1706        pyramid-mountain   
4862        pyramid-mountain   
6751   pyramid-mountain-peak   

                                            riding area  rating  distance  \
545                               Norse Peak Wilderness     NaN   4 miles   
501   Lake Chelan National Rec. Area (North Cascades...     NaN   2 miles   
1706                                       Port Angeles     NaN   3 miles   
4862                                 Mad River - Entiat     NaN  14 miles   
6751                                 Mad River - Entiat     NaN   3 miles   

        descent     climb  popularity_score Unnamed: 0             TITLE  \
545   -1,008 ft    855 ft                 0          0       Raven Roost   
501     -133 ft  1,218 ft                 0          9     Rainbow Ridge   
1706    -283 ft  2,671 ft                 0         15  Pyramid Mountain   
4862  -3,813 ft  4,841 ft                55         15  Pyramid Mountain   
6751    -274 ft  1,623 ft                95         15  Pyramid Mountain   

                  REGION  ...    GAIN HIGHEST RATING RATING_COUNT   LATITUDE  \
545   Mount Rainier Area  ...     NaN     NaN   2.75            4  47.008852   
501       North Cascades  ...  1700.0  5300.0   2.88            8  48.763431   
1706    Central Cascades  ...  3000.0  8243.0    3.0            4  48.018056   
4862    Central Cascades  ...  3000.0  8243.0    3.0            4  48.018056   
6751    Central Cascades  ...  3000.0  8243.0    3.0            4  48.018056   

       LONGITUDE REPORT_DATE REPORT_COUNT  \
545  -121.115564  2018-10-07            6   
501  -121.699677  2020-09-28           30   
1706 -120.505278  2020-08-01           44   
4862 -120.505278  2020-08-01           44   
6751 -120.505278  2020-08-01           44   

                                                    URL         title_wta  
545     https://www.wta.org/go-hiking/hikes/raven-roost       raven-roost  
501   https://www.wta.org/go-hiking/hikes/rainbow-ridge     rainbow-ridge  
1706  https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain  
4862  https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain  
6751  https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain  

[5 rows x 22 columns]

In [201]:
result_dataset = result_dataset.drop_duplicates()
result_dataset = result_dataset.dropna(subset=['TITLE'])
len(result_dataset['title_wta'].unique())

953

In [204]:
dataset_3 = trails_checkins[['Period','Check-Ins','trail']]
dataset_3['trail'] = dataset_3['trail'].str.replace('-trail','')
combined_trails = pd.merge(result_dataset,dataset_3.set_index('trail'),left_on='title',right_on='trail',how='inner')
combined_trails

title       riding area  rating  distance  descent  \
0        pyramid-mountain      Port Angeles     NaN   3 miles  -283 ft   
1        pyramid-mountain      Port Angeles     NaN   3 miles  -283 ft   
2        pyramid-mountain      Port Angeles     NaN   3 miles  -283 ft   
3        pyramid-mountain      Port Angeles     NaN   3 miles  -283 ft   
4        pyramid-mountain      Port Angeles     NaN   3 miles  -283 ft   
...                   ...               ...     ...       ...      ...   
1585457  enchanted-forest  Fisher Farm Park     NaN  1,576 ft   -27 ft   
1585458  enchanted-forest  Fisher Farm Park     NaN  1,576 ft   -27 ft   
1585459  enchanted-forest  Fisher Farm Park     NaN  1,576 ft   -27 ft   
1585460  enchanted-forest  Fisher Farm Park     NaN  1,576 ft   -27 ft   
1585461  enchanted-forest  Fisher Farm Park     NaN  1,576 ft   -27 ft   

            climb  popularity_score Unnamed: 0                   TITLE  \
0        2,671 ft                 0         15        Pyramid Mountain   
1        2,671 ft                 0         15        Pyramid Mountain   
2        2,671 ft                 0         15        Pyramid Mountain   
3        2,671 ft                 0         15        Pyramid Mountain   
4        2,671 ft                 0         15        Pyramid Mountain   
...           ...               ...        ...                     ...   
1585457     31 ft                95       3903  Enchanted Forest Trail   
1585458     31 ft                95       3903  Enchanted Forest Trail   
1585459     31 ft                95       3903  Enchanted Forest Trail   
1585460     31 ft                95       3903  Enchanted Forest Trail   
1585461     31 ft                95       3903  Enchanted Forest Trail   

                          REGION  ... RATING RATING_COUNT   LATITUDE  \
0               Central Cascades  ...    3.0            4  48.018056   
1               Central Cascades  ...    3.0            4  48.018056   
2               Central Cascades  ...    3.0            4  48.018056   
3               Central Cascades  ...    3.0            4  48.018056   
4               Central Cascades  ...    3.0            4  48.018056   
...                          ...  ...    ...          ...        ...   
1585457  Puget Sound and Islands  ...    0.0            0  48.988488   
1585458  Puget Sound and Islands  ...    0.0            0  48.988488   
1585459  Puget Sound and Islands  ...    0.0            0  48.988488   
1585460  Puget Sound and Islands  ...    0.0            0  48.988488   
1585461  Puget Sound and Islands  ...    0.0            0  48.988488   

          LONGITUDE REPORT_DATE REPORT_COUNT  \
0       -120.505278  2020-08-01           44   
1       -120.505278  2020-08-01           44   
2       -120.505278  2020-08-01           44   
3       -120.505278  2020-08-01           44   
4       -120.505278  2020-08-01           44   
...             ...         ...          ...   
1585457 -123.041787  2019-05-26            1   
1585458 -123.041787  2019-05-26            1   
1585459 -123.041787  2019-05-26            1   
1585460 -123.041787  2019-05-26            1   
1585461 -123.041787  2019-05-26            1   

                                                       URL         title_wta  \
0        https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain   
1        https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain   
2        https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain   
3        https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain   
4        https://www.wta.org/go-hiking/hikes/pyramid-mo...  pyramid-mountain   
...                                                    ...               ...   
1585457  https://www.wta.org/go-hiking/hikes/enchanted-...  enchanted-forest   
1585458  https://www.wta.org/go-hiking/hikes/enchanted-...  enchanted-forest   
1585459  https://www.wta.org/go-hiking/hikes/enchanted-...  enchanted-forest   
